In [1]:
#导入必要的爬虫包
import urllib
from urllib import parse
from urllib import request

import pandas as pd
#导入json包，后面解析json数据
import json

In [2]:
mykey = 'c19c3f153ec5df8943c5a36aff8a39a2'

In [15]:
#查询的接口地址
API_DISTRICT = 'https://restapi.amap.com/v3/config/district?'

'''
规则：只支持单个关键词语搜索关键词支持：行政区名称、citycode、adcode
例如，在subdistrict=2且showbiz=false时，搜索省份（例如山东），能够显示市（例如济南），区（例如历下区）
在subdistrict=1且showbiz=false时，搜索区（例如历下区）能够显示街道信息（例如舜华路街道）
'''
keywords = '厦门'

'''
规则：设置显示下级行政区级数（行政区级别包括：国家、省/直辖市、市、区/县4个级别）
可选值：0、1、2、3
0：不返回下级行政区；
1：返回下一级行政区；
2：返回下两级行政区；
3：返回下三级行政区；
'''
subdistrict = '1'

In [32]:
def request_district(ks, sub='0'):
    dict_param = {
        'key':mykey,#这个是我的开发者key，告诉高德这个数据是我抓的，每天会有限额，你们可以注册成为开发者，这样就有自己的key拉
        'keywords':ks,
        'subdistrict':sub,
        'showbiz':'false',
        'extensions':'all'}
    
    url_data = parse.urlencode(dict_param)
    url = API_DISTRICT+url_data
    
    #创建一个访问器
    request = urllib.request.Request(url)

    #访问网页
    response = urllib.request.urlopen(request)

    #读取网页内容
    webpage = response.read()

    #将内容用json解析
    result = json.loads(webpage.decode('utf8','ignore'))
    
    return result

In [16]:
#//restapi.amap.com/v3/config/district?
#key=您的key
#&keywords=湖里区
#&subdistrict=1
#&showbiz=false
#&extensions=all


#查询的条件
dict1 = {
    'key':mykey,#这个是我的开发者key，告诉高德这个数据是我抓的，每天会有限额，你们可以注册成为开发者，这样就有自己的key拉
    'keywords':keywords,
    'subdistrict':'3',
    'showbiz':'false',
    'extensions':'all'
    
#     's':'rsv3',
#     'output':'json',
#     'level':'district',
    
#     'platform':'JS',
#     'logversion':'2.0',
#     'sdkversion':'1.4.10'
}

#把查询条件组合成网页地址
url_data = parse.urlencode(dict1)
url = API_DISTRICT+url_data

#创建一个访问器
request = urllib.request.Request(url)

#访问网页
response = urllib.request.urlopen(request)

#读取网页内容
webpage = response.read()

#将内容用json解析
result = json.loads(webpage.decode('utf8','ignore'))

In [17]:
result

{'status': '1',
 'info': 'OK',
 'infocode': '10000',
 'count': '1',
 'suggestion': {'keywords': [], 'cities': []},
 'districts': [{'citycode': '0592',
   'adcode': '350200',
   'name': '厦门市',
   'polyline': '118.157144,24.553129;118.156304,24.55313;118.155265,24.553492;118.154711,24.553892;118.154468,24.554292;118.154589,24.554733;118.155022,24.555131;118.155663,24.555249;118.159413,24.555364;118.159889,24.555122;118.160054,24.554682;118.159976,24.554163;118.15846,24.553806;118.157741,24.553447;118.157144,24.553129|118.071342,24.435178;118.070291,24.435292;118.069543,24.435408;118.067936,24.435911;118.066362,24.436553;118.064181,24.436881;118.06252,24.437271;118.061373,24.43787;118.06066,24.438435;118.059791,24.439002;118.058304,24.440053;118.057156,24.441108;118.056634,24.442257;118.056348,24.444038;118.056522,24.445125;118.057661,24.44724;118.058826,24.449306;118.059461,24.450379;118.0604,24.452014;118.061035,24.452801;118.061835,24.453146;118.063599,24.453125;118.06486,24.453585;118

In [27]:
list_list_dis = []
for i in result['districts'][0]['districts']:
    t_list = [i['citycode'], i['adcode'], i['name'], i['center'], i['level']]
    list_list_dis.append(t_list)

In [28]:
df_district = pd.DataFrame(list_list_dis, columns=['citycode', 'adcode', 'name', 'center', 'level'])
df_district

citycode  adcode name                center     level
0     0592  350203  思明区  118.087828,24.462059  district
1     0592  350206  湖里区   118.10943,24.512764  district
2     0592  350213  翔安区  118.242811,24.637479  district
3     0592  350211  集美区  118.100869,24.572874  district
4     0592  350205  海沧区  118.036364,24.492512  district
5     0592  350212  同安区  118.150455,24.729333  district

In [35]:
df_district.dtypes

citycode    object
adcode      object
name        object
center      object
level       object
dtype: object

In [37]:
list_polyline = []
for rid, row in df_district.iterrows():
    t_r = request_district(str(row['name']))
    list_polyline.append(t_r['districts'][0]['polyline'])

In [ ]:
df_district['polyline'] = list_polyline

In [42]:
df_district

citycode  adcode name                center     level  \
0     0592  350203  思明区  118.087828,24.462059  district   
1     0592  350206  湖里区   118.10943,24.512764  district   
2     0592  350213  翔安区  118.242811,24.637479  district   
3     0592  350211  集美区  118.100869,24.572874  district   
4     0592  350205  海沧区  118.036364,24.492512  district   
5     0592  350212  同安区  118.150455,24.729333  district   

                                            polyline  
0  118.210671,24.481664;118.210924,24.482575;118....  
1  118.204456,24.504797;118.198133,24.502922;118....  
2  118.377091,24.554298;118.378859,24.55554;118.3...  
3  117.944548,24.750415;117.951303,24.746362;117....  
4  118.049015,24.418307;118.04383,24.418939;118.0...  
5  118.229502,24.831161;118.229207,24.827633;118....

In [71]:
import re

In [74]:
list_polygon = []
for rid, row in df_district.iterrows():
    t_list = re.split(';|\|', str(row['polyline']))
#     t_polygon = [tuple([x.split(',')[1], x.split(',')[0]]) for x in t_list]
#     list_polygon.append(t_polygon)

    t_polygon = []
    for x in t_list:
        t_co = list(x.split(','))
        t_tup = tuple([float(t_co[1]), float(t_co[0])])
        t_polygon.append(t_tup)
    
    list_polygon.append(t_polygon)

In [75]:
df_district['polygon'] = list_polygon
df_district

citycode  adcode name                center     level  \
0     0592  350203  思明区  118.087828,24.462059  district   
1     0592  350206  湖里区   118.10943,24.512764  district   
2     0592  350213  翔安区  118.242811,24.637479  district   
3     0592  350211  集美区  118.100869,24.572874  district   
4     0592  350205  海沧区  118.036364,24.492512  district   
5     0592  350212  同安区  118.150455,24.729333  district   

                                            polyline  \
0  118.210671,24.481664;118.210924,24.482575;118....   
1  118.204456,24.504797;118.198133,24.502922;118....   
2  118.377091,24.554298;118.378859,24.55554;118.3...   
3  117.944548,24.750415;117.951303,24.746362;117....   
4  118.049015,24.418307;118.04383,24.418939;118.0...   
5  118.229502,24.831161;118.229207,24.827633;118....   

                                             polygon  
0  [(24.481664, 118.210671), (24.482575, 118.2109...  
1  [(24.504797, 118.204456), (24.502922, 118.1981...  
2  [(24.554298, 118.377091), (24.55554, 118.37885...  
3  [(24.750415, 117.944548), (24.746362, 117.9513...  
4  [(24.418307, 118.049015), (24.418939, 118.0438...  
5  [(24.831161, 118.229502), (24.827633, 118.2292...

In [76]:
df_district.to_csv('data/xm_district.csv', index=False)

In [60]:
import ast
# list(ast.literal_eval('(2,3,4),(1,6,7)'))
ast.literal_eval('[(2,3,4),(1,6,7)]')

[(2, 3, 4), (1, 6, 7)]

In [77]:
for rid, row in df_district.iterrows():
    print(row['polygon'])

[(24.481664, 118.210671), (24.482575, 118.210924), (24.483207, 118.211168), (24.483427, 118.211308), (24.48355, 118.211628), (24.483524, 118.211867), (24.483371, 118.212103), (24.483107, 118.212269), (24.482802, 118.212303), (24.482066, 118.212177), (24.481362, 118.211909), (24.481117, 118.211661), (24.481035, 118.211396), (24.481046, 118.2111), (24.481211, 118.210802), (24.481406, 118.210685), (24.481664, 118.210671), (24.435178, 118.071342), (24.435292, 118.070291), (24.435408, 118.069543), (24.435911, 118.067936), (24.436553, 118.066362), (24.436881, 118.064181), (24.437271, 118.06252), (24.43787, 118.061373), (24.438435, 118.06066), (24.439002, 118.059791), (24.440053, 118.058304), (24.441108, 118.057156), (24.442257, 118.056634), (24.444038, 118.056348), (24.445125, 118.056522), (24.44724, 118.057661), (24.449306, 118.058826), (24.450379, 118.059461), (24.452014, 118.0604), (24.452801, 118.061035), (24.453146, 118.061835), (24.453125, 118.063599), (24.453585, 118.06486), (24.45377

In [78]:
import folium

In [90]:
# Sydney lat&long
lat = 24.651386
long = 118.129117

# define xm map
map_xm = folium.Map(location=[lat, long], zoom_start=10)

# for rid, row in df_district.iterrows():
#     folium.GeoJson('data/district/'+ str(row['name']) + '.geojson', name='geojson').add_to(map_xm)

folium.GeoJson('data/district/xm.geojson', name='geojson').add_to(map_xm)


map_xm

In [95]:
lat = 24.651386
long = 118.129117

# define xm map
map_xm = folium.Map(location=[lat, long], zoom_start=10)

# for rid, row in df_district.iterrows():
#     folium.GeoJson('data/district/'+ str(row['name']) + '.geojson', name='geojson').add_to(map_xm)

folium.GeoJson('data/roadnetwork/roads.geojson', name='geojson').add_to(map_xm)


map_xm